<a href="https://colab.research.google.com/github/Ruqyai/MENADD-DL/blob/main/RNN/Music_Gerenation_with_LSTM.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

### Music gereration 
Plan was simple:
1. Read midi file, convert it to matrix of features
2. Create simple model with Keras and LSTM to learn the pattern
3. Use subsample of initial midi file as a input for model to generate pure art
4. Save prediction from model to midi file


In [1]:
!pip install mido

     |████████████████████████████████| 51 kB 2.3 MB/s 


In [2]:
import mido
from mido import MidiFile, MidiTrack, Message
from tensorflow.keras.layers import LSTM, Dense, Activation, Dropout, Flatten
from tensorflow.keras.preprocessing import sequence
from tensorflow.keras.models import Sequential
from tensorflow.keras.optimizers import Adam
from sklearn.preprocessing import MinMaxScaler
import numpy as np

##### Read midi file

In [3]:
!wget https://github.com/Ruqyai/MENADD-DL/raw/main/Data/Piano.mid

--2021-10-12 09:07:05--  https://github.com/Ruqyai/MENADD-DL/raw/main/Data/Piano.mid
Resolving github.com (github.com)... 140.82.113.4
Connecting to github.com (github.com)|140.82.113.4|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/Ruqyai/MENADD-DL/main/Data/Piano.mid [following]
--2021-10-12 09:07:05--  https://raw.githubusercontent.com/Ruqyai/MENADD-DL/main/Data/Piano.mid
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 385284 (376K) [audio/midi]
Saving to: ‘Piano.mid’

Piano.mid           100%[===================>] 376.25K  --.-KB/s    in 0.03s   

2021-10-12 09:07:05 (10.5 MB/s) - ‘Piano.mid’ saved [385284/385284]



In [4]:
mid = MidiFile('Piano.mid') 
mid

MidiFile(type=1, ticks_per_beat=256, tracks=[
  MidiTrack([
    MetaMessage('set_tempo', tempo=500000, time=0),
    MetaMessage('track_name', name='<Title>', time=0),
    MetaMessage('copyright', text='@<copyright>', time=0),
    MetaMessage('end_of_track', time=0)]),
  MidiTrack([
    MetaMessage('track_name', name='Piano (Left Hand)', time=0),
    Message('control_change', channel=0, control=7, value=127, time=0),
    Message('control_change', channel=0, control=10, value=64, time=0),
    Message('control_change', channel=0, control=0, value=0, time=0),
    Message('control_change', channel=0, control=32, value=0, time=0),
    Message('program_change', channel=0, program=0, time=0),
    Message('control_change', channel=0, control=93, value=0, time=0),
    MetaMessage('time_signature', numerator=4, denominator=4, clocks_per_click=24, notated_32nd_notes_per_beat=8, time=0),
    MetaMessage('key_signature', key='Eb', time=0),
    Message('control_change', channel=0, control=93, value=0

##### Extract notes sequence

In [5]:
notes = []
for msg in mid:
    if not msg.is_meta and msg.channel == 0 and msg.type == 'note_on':
        data = msg.bytes()
        notes.append(data[1])

In [6]:
notes

[51,
 63,
 50,
 62,
 48,
 60,
 46,
 58,
 51,
 63,
 46,
 58,
 48,
 60,
 46,
 58,
 50,
 62,
 46,
 58,
 48,
 60,
 49,
 61,
 50,
 62,
 46,
 58,
 51,
 63,
 46,
 58,
 51,
 63,
 50,
 62,
 48,
 60,
 46,
 58,
 51,
 63,
 46,
 58,
 48,
 60,
 46,
 58,
 50,
 62,
 48,
 60,
 46,
 58,
 48,
 60,
 50,
 62,
 46,
 58,
 51,
 63,
 46,
 58,
 39,
 46,
 51,
 53,
 55,
 51,
 58,
 63,
 44,
 51,
 56,
 58,
 60,
 56,
 63,
 68,
 46,
 53,
 58,
 60,
 62,
 58,
 65,
 70,
 41,
 44,
 50,
 53,
 58,
 62,
 65,
 70,
 51,
 46,
 39,
 46,
 51,
 53,
 55,
 51,
 58,
 63,
 44,
 51,
 56,
 58,
 60,
 56,
 63,
 68,
 46,
 53,
 58,
 60,
 62,
 58,
 65,
 70,
 39,
 46,
 51,
 55,
 58,
 63,
 67,
 70,
 75,
 51,
 63,
 50,
 62,
 48,
 60,
 46,
 58,
 51,
 63,
 46,
 58,
 48,
 60,
 46,
 58,
 50,
 62,
 46,
 58,
 48,
 60,
 49,
 61,
 50,
 62,
 46,
 58,
 51,
 63,
 46,
 58,
 51,
 63,
 50,
 62,
 48,
 60,
 46,
 58,
 51,
 63,
 46,
 58,
 48,
 60,
 46,
 58,
 50,
 62,
 48,
 60,
 46,
 58,
 48,
 60,
 50,
 62,
 46,
 58,
 51,
 63,
 46,
 58,
 39,
 46,
 51,
 53,
 55,


#### Apply min-max scalling

In [7]:
scaler = MinMaxScaler(feature_range=(0,1))
scaler.fit(np.array(notes).reshape(-1,1))
notes = list(scaler.transform(np.array(notes).reshape(-1,1)))

In [8]:
notes

[array([0.33333333]),
 array([0.66666667]),
 array([0.30555556]),
 array([0.63888889]),
 array([0.25]),
 array([0.58333333]),
 array([0.19444444]),
 array([0.52777778]),
 array([0.33333333]),
 array([0.66666667]),
 array([0.19444444]),
 array([0.52777778]),
 array([0.25]),
 array([0.58333333]),
 array([0.19444444]),
 array([0.52777778]),
 array([0.30555556]),
 array([0.63888889]),
 array([0.19444444]),
 array([0.52777778]),
 array([0.25]),
 array([0.58333333]),
 array([0.27777778]),
 array([0.61111111]),
 array([0.30555556]),
 array([0.63888889]),
 array([0.19444444]),
 array([0.52777778]),
 array([0.33333333]),
 array([0.66666667]),
 array([0.19444444]),
 array([0.52777778]),
 array([0.33333333]),
 array([0.66666667]),
 array([0.30555556]),
 array([0.63888889]),
 array([0.25]),
 array([0.58333333]),
 array([0.19444444]),
 array([0.52777778]),
 array([0.33333333]),
 array([0.66666667]),
 array([0.19444444]),
 array([0.52777778]),
 array([0.25]),
 array([0.58333333]),
 array([0.19444444

#### Prepare features for training and data subsample for prediction

In [9]:
# LSTM layers requires that data must have a certain shape
# create list of lists fist
notes = [list(note) for note in notes]
# subsample data for training and prediction
X = []
y = []
# number of notes in a batch
n_prev = 30
for i in range(len(notes)-n_prev):
    X.append(notes[i:i+n_prev])
    y.append(notes[i+n_prev])
# save a seed to do prediction later
X_test = X[-300:]
X = X[:-300]
y = y[:-300]

In [10]:
notes

[[0.33333333333333326],
 [0.6666666666666667],
 [0.3055555555555556],
 [0.6388888888888888],
 [0.25],
 [0.5833333333333333],
 [0.19444444444444442],
 [0.5277777777777777],
 [0.33333333333333326],
 [0.6666666666666667],
 [0.19444444444444442],
 [0.5277777777777777],
 [0.25],
 [0.5833333333333333],
 [0.19444444444444442],
 [0.5277777777777777],
 [0.3055555555555556],
 [0.6388888888888888],
 [0.19444444444444442],
 [0.5277777777777777],
 [0.25],
 [0.5833333333333333],
 [0.2777777777777777],
 [0.6111111111111112],
 [0.3055555555555556],
 [0.6388888888888888],
 [0.19444444444444442],
 [0.5277777777777777],
 [0.33333333333333326],
 [0.6666666666666667],
 [0.19444444444444442],
 [0.5277777777777777],
 [0.33333333333333326],
 [0.6666666666666667],
 [0.3055555555555556],
 [0.6388888888888888],
 [0.25],
 [0.5833333333333333],
 [0.19444444444444442],
 [0.5277777777777777],
 [0.33333333333333326],
 [0.6666666666666667],
 [0.19444444444444442],
 [0.5277777777777777],
 [0.25],
 [0.5833333333333333],

#### Made sequential model with several layers, use LSTM as it time dependent data



In [11]:
model = Sequential()
model.add(LSTM(256, input_shape=(n_prev, 1), return_sequences=True))
model.add(Dropout(0.6))
model.add(LSTM(128, input_shape=(n_prev, 1), return_sequences=True))
model.add(Dropout(0.6))
model.add(LSTM(64, input_shape=(n_prev, 1), return_sequences=False))
model.add(Dropout(0.6))
model.add(Dense(1))
model.add(Activation('linear'))

model.compile(loss='mse', optimizer=Adam(learning_rate=0.001))


#### Train your model.
It might take a while, I was waiting for 1 hour with just 5 epoch

In [12]:
model.fit(np.array(X), np.array(y), batch_size=32, epochs=3, verbose=1)

Epoch 1/3
400/400 [==============================] - 81s 189ms/step - loss: 0.0521
Epoch 2/3
400/400 [==============================] - 76s 190ms/step - loss: 0.0469
Epoch 3/3
400/400 [==============================] - 75s 188ms/step - loss: 0.0451


#### Make a prediction

In [13]:
prediction = model.predict(np.array(X_test))
prediction = np.squeeze(prediction)
prediction = np.squeeze(scaler.inverse_transform(prediction.reshape(-1,1)))
prediction = [int(i) for i in prediction]

In [14]:
#prediction

#### Save your result to new midi file

In [15]:
mid = MidiFile()
track = MidiTrack()
t = 0
for note in prediction:
    # 147 means note_on
    # 67 is velosity
    note = np.asarray([147, note, 67])
    bytes = note.astype(int)
    #print(bytes)
    msg = Message.from_bytes(bytes[0:3])
    t += 1
    msg.time = t
    track.append(msg)
    #print(msg)
mid.tracks.append(track)
mid.save('Music_gerenation.mid')

In [16]:
from IPython.display import Audio
Audio("Music_gerenation.mid")